In [2]:
import tensorflow as tf
gpus=tf.config.list_physical_devices('GPU')
gpus

[PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]

In [1]:
from tensorflow.keras.applications import Xception,EfficientNetB0,EfficientNetB1, ResNet50
from tensorflow.keras.applications.xception import preprocess_input
import pandas as pd
import numpy as np
from tensorflow.keras.models import Sequential,Model
from tensorflow.keras.layers import Dense, Dropout,Conv2D, MaxPooling2D, Flatten, BatchNormalization, GlobalAveragePooling2D
from tensorflow.keras.utils import image_dataset_from_directory
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.losses import categorical_crossentropy
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping, ReduceLROnPlateau
from tensorflow.keras.optimizers import Adam, Adamax
from tensorflow.keras.metrics import Precision,Recall
import tensorflow as tf
import matplotlib.pyplot as plt
from keras.layers import Lambda, Input
batch_size=16
img_size=(224,224)
SEED=111
tf.keras.utils.set_random_seed(SEED)
tf.random.set_seed(SEED)
np.random.seed(SEED)

2024-07-01 22:20:56.961457: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-07-01 22:20:59.454507: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-07-01 22:21:01.939389: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [2]:
# Define the paths
dataset_dir = 'new folder'

# Create an ImageDataGenerator for data augmentation and rescaling
train_datagen = ImageDataGenerator(
    rescale=1.0/255.0,          # Normalize pixel values
    rotation_range=20,          # Randomly rotate images
    width_shift_range=0.2,      # Randomly shift images horizontally
    height_shift_range=0.2,     # Randomly shift images vertically
    shear_range=0.2,            # Randomly shear images
    zoom_range=0.2,             # Randomly zoom into images
    horizontal_flip=True,       # Randomly flip images horizontally
    validation_split=0.2,# Use 20% of the data for validation
)

# Create a separate ImageDataGenerator for the test data (without augmentation)
test_datagen = ImageDataGenerator(rescale=1.0/255.0)

# Load and iterate training dataset
train_data = train_datagen.flow_from_directory(
    dataset_dir+'/training',
    target_size=(224, 224),       # Resize images to match EfficientNet input size
    batch_size=batch_size,
    class_mode='binary',          # Binary classification
    subset='training'             # Set as training data
)

# Load and iterate validation dataset
val_data= train_datagen.flow_from_directory(
    dataset_dir+'/training',
    target_size=(224, 224),
    batch_size=batch_size,
    class_mode='binary',
    subset='validation'           # Set as validation data
)

# Load and iterate test dataset
test_data = test_datagen.flow_from_directory(
    dataset_dir+'/testing',
    target_size=(224, 224),
    batch_size=batch_size,
    class_mode='binary',
    subset=None,                  # Not a subset, use all remaining data
    shuffle=False                 # Don't shuffle for evaluation/prediction
)

Found 10148 images belonging to 2 classes.
Found 2536 images belonging to 2 classes.
Found 7314 images belonging to 2 classes.


In [3]:
# Define the model
img_shape = (img_size[0], img_size[1], 3)

# Define input layer
input_layer = Input(shape=img_shape)

# Load Xception base model with imagenet weights
base_model = EfficientNetB0(include_top=False, weights="imagenet", input_shape=img_shape, pooling='max')

# Add custom layers on top of the base model using the Functional API
x = base_model(input_layer)
x = Flatten()(x)
x = Dropout(rate=0.3)(x)
x = Dense(128, activation='relu')(x)
x = Dropout(rate=0.25)(x)
output_layer = Dense(1, activation='sigmoid')(x)

# Combine into a new model
model = Model(inputs=input_layer, outputs=output_layer)
# Compile the model
model.compile(optimizer=Adamax(learning_rate=0.001),
              loss='binary_crossentropy',
              metrics=['accuracy', Precision(), Recall()])

# Show the model summary
model.summary()

2024-07-01 22:21:07.586834: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-07-01 22:21:08.801038: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-07-01 22:21:08.801112: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-07-01 22:21:08.813752: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-07-01 22:21:08.813814: I external/local_xla/xla/stream_executor

Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer (InputLayer)        │ (None, 224, 224, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ efficientnetb0 (Functional)     │ (None, 1280)           │     4,049,571 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten (Flatten)               │ (None, 1280)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 1280)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 128)            │       163,968 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 1)              │           129 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 4,213,668 (16.07 MB)

 Trainable params: 4,171,645 (15.91 MB)

 Non-trainable params: 42,023 (164.16 KB)

In [4]:
history = model.fit(train_data,
                    steps_per_epoch=train_data.samples//batch_size,
                    validation_data=val_data,
                    validation_steps=val_data.samples//batch_size,
                    epochs=10)

# Evaluate the model on the test data
test_loss, test_accuracy, test_precision, test_recall = model.evaluate(test_data)
print(f"Test Accuracy: {test_accuracy}")
print(f"Test Precision: {test_precision}")
print(f"Test Recall: {test_recall}")

Epoch 1/10


/home/tf-gpu/anaconda3/envs/tensorflow/lib/python3.12/site-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()
I0000 00:00:1719852699.494702   49671 service.cc:145] XLA service 0x7f7c200027c0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
I0000 00:00:1719852699.495086   49671 service.cc:153]   StreamExecutor device (0): NVIDIA GeForce RTX 3050 Laptop GPU, Compute Capability 8.6
2024-07-01 22:21:40.744333: I tensorflow/compiler/mlir/tensorflow/utils/dump_mlir_util.cc:268] disabling MLIR crash reproducer, set env var `MLIR_CRASH_REPRODUCER_DIRECTORY` to enable.
2024-07-01 22:21:43.553746: I external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:465] Loaded cuDNN 

626/634 ━━━━━━━━━━━━━━━━━━━━ 1s 245ms/step - accuracy: 0.9594 - loss: 0.3136 - precision: 0.9607 - recall: 0.9565

I0000 00:00:1719852992.544623   49671 asm_compiler.cc:369] ptxas warning : Registers are spilled to local memory in function 'input_reduce_fusion', 28 bytes spill stores, 28 bytes spill loads
ptxas warning : Registers are spilled to local memory in function 'input_reduce_fusion_1', 32 bytes spill stores, 32 bytes spill loads
ptxas warning : Registers are spilled to local memory in function 'input_reduce_fusion_327', 44 bytes spill stores, 44 bytes spill loads
ptxas warning : Registers are spilled to local memory in function 'input_reduce_fusion_4', 12 bytes spill stores, 12 bytes spill loads



634/634 ━━━━━━━━━━━━━━━━━━━━ 363s 427ms/step - accuracy: 0.9597 - loss: 0.3109 - precision: 0.9610 - recall: 0.9568 - val_accuracy: 0.9858 - val_loss: 0.0610 - val_precision: 0.9992 - val_recall: 0.9723
Epoch 2/10
  1/634 ━━━━━━━━━━━━━━━━━━━━ 2:27 234ms/step - accuracy: 1.0000 - loss: 0.0056 - precision: 1.0000 - recall: 1.0000

...

634/634 ━━━━━━━━━━━━━━━━━━━━ 186s 289ms/step - accuracy: 0.9901 - loss: 0.0499 - precision: 0.9960 - recall: 0.9841 - val_accuracy: 0.9917 - val_loss: 0.0350 - val_precision: 0.9906 - val_recall: 0.9929
Epoch 8/10
634/634 ━━━━━━━━━━━━━━━━━━━━ 0s 97us/step - accuracy: 1.0000 - loss: 0.0080 - precision: 1.0000 - recall: 1.0000 - val_accuracy: 1.0000 - val_loss: 0.0059 - val_precision: 1.0000 - val_recall: 1.0000
Epoch 9/10


2024-07-01 22:36:43.444886: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node IteratorGetNext}}]]
2024-07-01 22:36:43.446181: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node IteratorGetNext}}]]
	 [[IteratorGetNext/_2]]
2024-07-01 22:36:43.489994: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node IteratorGetNext}}]]
2024-07-01 22:36:43.490184: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node IteratorGetNext}}]]
	 [[IteratorGetNext/_4]]


634/634 ━━━━━━━━━━━━━━━━━━━━ 187s 291ms/step - accuracy: 0.9919 - loss: 0.0421 - precision: 0.9962 - recall: 0.9874 - val_accuracy: 0.9917 - val_loss: 0.0445 - val_precision: 0.9960 - val_recall: 0.9874
Epoch 10/10
634/634 ━━━━━━━━━━━━━━━━━━━━ 0s 85us/step - accuracy: 1.0000 - loss: 9.1518e-04 - precision: 1.0000 - recall: 1.0000 - val_accuracy: 1.0000 - val_loss: 0.0257 - val_precision: 1.0000 - val_recall: 1.0000


2024-07-01 22:39:50.314224: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node IteratorGetNext}}]]
2024-07-01 22:39:50.315207: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node IteratorGetNext}}]]
	 [[IteratorGetNext/_2]]
2024-07-01 22:39:50.350093: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node IteratorGetNext}}]]
2024-07-01 22:39:50.350328: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node IteratorGetNext}}]]
	 [[IteratorGetNext/_4]]


458/458 ━━━━━━━━━━━━━━━━━━━━ 81s 178ms/step - accuracy: 0.9940 - loss: 0.0199 - precision: 0.4895 - recall: 0.5014
Test Accuracy: 0.9960349798202515
Test Precision: 0.9948172569274902
Test Recall: 0.9972655177116394


In [1]:
model.save("ResNet1(clot10).keras")

NameError: name 'model' is not defined

In [ ]:
model.evaluate(test_data)

In [5]:
y_pred=model.predict(test_data)

458/458 ━━━━━━━━━━━━━━━━━━━━ 81s 161ms/step


In [6]:
y_pred_classes = (y_pred > 0.5).astype("int32")

In [7]:
from sklearn.metrics import confusion_matrix
# Calculate confusion matrix
tn, fp, fn, tp = confusion_matrix(test_data.classes, y_pred_classes).ravel()

# Calculate sensitivity and specificity
sensitivity = tp / (tp + fn)
specificity = tn / (tn + fp)

print(f'Sensitivity: {sensitivity}')
print(f'Specificity: {specificity}')

Sensitivity: 0.9972655181843041
Specificity: 0.9948044845501778


In [5]:
from tensorflow.keras.layers import Input, GlobalAveragePooling2D, Dense, Dropout
from tensorflow.keras.models import Model
from tensorflow.keras.applications import EfficientNetB1
from collections import defaultdict
import visualkeras
from PIL import ImageFont, Image

# Define class names
class_names = ["glioma", "meningioma", "notumor", "pituitary"]

# Load the EfficientNetB1 model, excluding the top fully connected layers
base_model = EfficientNetB1(include_top=False, weights='imagenet', input_shape=(240, 240, 3))

# Freeze the base model
base_model.trainable = False

# Add new classification layers
x = base_model.output
x = GlobalAveragePooling2D()(x)
x = Dense(512, activation='relu')(x)
x = Dropout(0.5)(x)
x = Dense(128, activation='relu')(x)
x = Dropout(0.5)(x)
output_layer = Dense(len(class_names), activation='softmax')(x)

# Create the model
model = Model(inputs=base_model.input, outputs=output_layer)

# Define color map with improved colors
color_map = defaultdict(dict)
color_map[Input]['fill'] = '#FF6F59'
color_map[GlobalAveragePooling2D]['fill'] = '#9134ED'  # Gray
color_map[Dense]['fill'] = '#011627'  # Purple
color_map[Dropout]['fill'] = '#941C2F'  # Red

# Load font
try:
    font_path = 'Roboto-Regular.ttf'  # Update this path if necessary
    font = ImageFont.truetype(font_path, 300)
except OSError:
    # Fallback to a default font if the specified font is not found
    font = ImageFont.load_default(size=300)

# Visualize the model with scaled x-axis
visualkeras.layered_view(model, to_file='efficientnetb1.png', legend=True, font=font, color_map=color_map, scale_xy=100)


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.7/11.7 MB 1.3 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.1/13.1 MB 2.8 MB/s eta 0:00:0000:0100:01


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 3.6 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.2/10.2 MB 3.6 MB/s eta 0:00:0000:010:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 751.2/751.2 kB 4.3 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.
